In [1]:
import numpy as np
import h5py
import glob
from pycbc import conversions
from pycbc import coordinates

In [2]:
path = ['./shilpadata','./yifandata','./sumitdata','./bnsdata']
posfile = []
for p in path:
    f = glob.glob(p+'/*.hdf')
    posfile.extend(f)

In [3]:
def custom_sort(name):
    return name.split('/')[2]
#the 0th is dot, 1st is person name, 2nd is GW event name

def extract_quantile(sample):
    return np.quantile(sample,0.5), np.quantile(sample,0.95) - np.quantile(sample,0.5), \
                                             np.quantile(sample,0.5) - np.quantile(sample,0.05)

In [4]:
def latexpm(num,p,m,nround=1):
    if nround == 0:
        num,p,m = round(num),round(p),round(m)
    else:
        num,p,m = round(num,nround),round(p,nround),round(m,nround)
    return str(r'$'+str(num)+r'^{+'+str(p)+r'}_{-'+str(m)+r'}$')

In [5]:
posfile.sort(key=custom_sort)

In [6]:
posfile

['./shilpadata/GW150914_095045-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW151012_095443-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW151226_033853-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW170104_101158-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW170121_212536-PYCBC-POSTERIOR-XPHM.hdf',
 './yifandata/GW170202_135657-PYCBC-POSTERIOR-XPHM.hdf',
 './yifandata/GW170304_163753-PYCBC-POSTERIOR-XPHM.hdf',
 './sumitdata/GW170403_230611-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW170608_020116-PYCBC-POSTERIOR-XPHM.hdf',
 './yifandata/GW170727_010430-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW170729_185629-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW170809_082821-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW170814_103043-PYCBC-POSTERIOR-XPHM.hdf',
 './bnsdata/GW170817_124104-PYCBC-POSTERIOR-PHENOMDNRT.hdf',
 './yifandata/GW170818_022509-PYCBC-POSTERIOR-XPHM.hdf',
 './shilpadata/GW170823_131358-PYCBC-POSTERIOR-XPHM.hdf',
 './yifandata/GW190408_181802-PYCBC-POSTERIOR-XPHM.hdf',
 './yifandata/GW1

In [7]:
np.size(posfile)

57

In [8]:
for i,path in enumerate(posfile):
    f = h5py.File(path,'r')
    #print('Analyzing the '+str(i)+'th event:'+path)
    #name
    oldname = path.split('/')[2].split('-')[0]
    #name = oldname[:8]+r'\_' +oldname[9:11]+':'+oldname[11:13]+':'+oldname[13:15]
    name = oldname[:8]+r'\_'+oldname[9:]
    if name == 'GW170817\_124104' or name =='GW190425\_081805':
        srcmass1,srcmass1plus,srcmass1minus = extract_quantile(f['samples']['srcmass1']) 
        srcmass2,srcmass2plus,srcmass2minus = extract_quantile(f['samples']['srcmass2'])
        srcmchirp,srcmchirpplus,srcmchirpminus = extract_quantile(f['samples']['srcmchirp'])
        q,qplus,qminus = extract_quantile(f['samples']['q'])
        chieff,chieffplus,chieffminus = extract_quantile(f['samples']['chi_eff'])
        distance,distanceplus,distanceminus = extract_quantile(f['samples']['distance'])
        z,zplus,zminus = extract_quantile(f['samples']['redshift'])
        snr = np.max(conversions.snr_from_loglr(f['samples']['loglikelihood']-f['samples'].attrs['lognl']))
        snr = round(snr,1)
        contents = str(i+1)+r'& $\mathrm{'+name+r'}$ & '+latexpm(srcmass1,srcmass1plus,srcmass1minus)+' & '\
         +latexpm(srcmass2,srcmass2plus,srcmass2minus)+' & '\
         +latexpm(srcmchirp,srcmchirpplus,srcmchirpminus,3)+' & '\
         +latexpm(q,qplus,qminus)+' & '\
         +latexpm(chieff,chieffplus,chieffminus,2)+' & '\
         +latexpm(distance,distanceplus,distanceminus,0)+' & '\
         +latexpm(z,zplus,zminus,2)+' & '\
         ' - & '\
         ' - & '\
         +str(snr)+r' \\ '
    else:
    #m1,m2,mc,q
        srcmass1,srcmass1plus,srcmass1minus = extract_quantile(f['samples']['srcmass1']) 
        srcmass2,srcmass2plus,srcmass2minus = extract_quantile(f['samples']['srcmass2'])
        srcmchirp,srcmchirpplus,srcmchirpminus = extract_quantile(f['samples']['srcmchirp'])
        q,qplus,qminus = extract_quantile(f['samples']['q'])
    
    #chieff,chip
        chieff,chieffplus,chieffminus = extract_quantile(f['samples']['chi_eff'])
        chip,chipplus,chipminus = extract_quantile(f['samples']['chi_p'])
    
    #distance,z
        distance,distanceplus,distanceminus = extract_quantile(f['samples']['distance'])
        z,zplus,zminus = extract_quantile(f['samples']['redshift'])
    
    #Cartesian spin
        spin1_x,spin1_y,spin1_z = coordinates.spherical_to_cartesian(f['samples']['spin1_a'], \
                                                              f['samples']['spin1_azimuthal'],\
                                                              f['samples']['spin1_polar'])
        spin2_x,spin2_y,spin2_z = coordinates.spherical_to_cartesian(f['samples']['spin2_a'], \
                                                              f['samples']['spin2_azimuthal'],\
                                                              f['samples']['spin2_polar'])
    # final mass
        mfsample = conversions.final_mass_from_initial(mass1=f['samples']['srcmass1'],\
                                                   mass2=f['samples']['srcmass2'],\
                                                   spin1x=spin1_x,spin1y=spin1_y,spin1z=spin1_z,\
                                                   spin2x=spin2_x,spin2y=spin2_y,spin2z=spin2_z,\
                                                   approximant='SEOBNRv4')
        mf,mfplus,mfminus = extract_quantile(mfsample)
    #final spin
        chifsample = conversions.final_spin_from_initial(mass1=f['samples']['srcmass1'],\
                                                   mass2=f['samples']['srcmass2'],\
                                                   spin1x=spin1_x,spin1y=spin1_y,spin1z=spin1_z,\
                                                   spin2x=spin2_x,spin2y=spin2_y,spin2z=spin2_z,\
                                                   approximant='SEOBNRv4')
        chif,chifplus,chifminus = extract_quantile(chifsample)
    #snr
        snr = np.max(conversions.snr_from_loglr(f['samples']['loglikelihood']-f['samples'].attrs['lognl']))
        snr = round(snr,1)
        
        if i+1 in [42,52,54,55]:
            contents = str(i+1)+r'& $\textbf{'+name+r'}$ & '+latexpm(srcmass1,srcmass1plus,srcmass1minus)+' & '\
         +latexpm(srcmass2,srcmass2plus,srcmass2minus)+' & '\
         +latexpm(srcmchirp,srcmchirpplus,srcmchirpminus)+' & '\
         +latexpm(q,qplus,qminus)+' & '\
         +latexpm(chieff,chieffplus,chieffminus,2)+' & '\
         +latexpm(distance,distanceplus,distanceminus,0)+' & '\
         +latexpm(z,zplus,zminus,2)+' & '\
         +latexpm(mf,mfplus,mfminus)+' & '\
         +latexpm(chif,chifplus,chifminus,2)+' & '\
         +str(snr)+r' \\ '
        else:
            contents = str(i+1)+r'& $\mathrm{'+name+r'}$ & '+latexpm(srcmass1,srcmass1plus,srcmass1minus)+' & '\
         +latexpm(srcmass2,srcmass2plus,srcmass2minus)+' & '\
         +latexpm(srcmchirp,srcmchirpplus,srcmchirpminus)+' & '\
         +latexpm(q,qplus,qminus)+' & '\
         +latexpm(chieff,chieffplus,chieffminus,2)+' & '\
         +latexpm(distance,distanceplus,distanceminus,0)+' & '\
         +latexpm(z,zplus,zminus,2)+' & '\
         +latexpm(mf,mfplus,mfminus)+' & '\
         +latexpm(chif,chifplus,chifminus,2)+' & '\
         +str(snr)+r' \\ '
    if ((i+1) % 2) == 0:
        contents = r'\rowcolor{Gray}' + contents

    print(contents)
    f.close()


1& $\mathrm{GW150914\_095045}$ & $34.7^{+4.7}_{-2.8}$ & $29.8^{+2.8}_{-4.4}$ & $27.9^{+1.4}_{-1.3}$ & $1.2^{+0.4}_{-0.1}$ & $-0.03^{+0.11}_{-0.13}$ & $534^{+123}_{-157}$ & $0.11^{+0.02}_{-0.03}$ & $61.5^{+2.9}_{-2.7}$ & $0.67^{+0.03}_{-0.05}$ & 23.8 \\ 
\rowcolor{Gray}2& $\mathrm{GW151012\_095443}$ & $27.0^{+10.5}_{-7.9}$ & $11.8^{+4.3}_{-3.1}$ & $15.2^{+1.1}_{-0.9}$ & $2.3^{+2.0}_{-1.1}$ & $0.05^{+0.22}_{-0.15}$ & $927^{+456}_{-329}$ & $0.18^{+0.08}_{-0.06}$ & $37.4^{+7.7}_{-4.8}$ & $0.62^{+0.08}_{-0.08}$ & 9.8 \\ 
3& $\mathrm{GW151226\_033853}$ & $14.1^{+10.3}_{-3.4}$ & $7.4^{+2.2}_{-2.6}$ & $8.8^{+0.2}_{-0.2}$ & $1.9^{+3.2}_{-0.8}$ & $0.22^{+0.21}_{-0.08}$ & $503^{+133}_{-156}$ & $0.11^{+0.03}_{-0.03}$ & $20.5^{+7.9}_{-1.5}$ & $0.72^{+0.03}_{-0.03}$ & 13.2 \\ 
\rowcolor{Gray}4& $\mathrm{GW170104\_101158}$ & $29.1^{+6.3}_{-4.4}$ & $20.5^{+4.2}_{-4.3}$ & $21.0^{+1.9}_{-1.5}$ & $1.4^{+0.7}_{-0.4}$ & $-0.06^{+0.15}_{-0.18}$ & $1077^{+384}_{-458}$ & $0.21^{+0.07}_{-0.08}$ & $47.5^{+4.2}_

33& $\mathrm{GW190602\_175927}$ & $70.6^{+16.9}_{-13.4}$ & $43.6^{+14.4}_{-17.3}$ & $47.3^{+8.4}_{-8.7}$ & $1.6^{+1.6}_{-0.5}$ & $0.12^{+0.24}_{-0.27}$ & $2897^{+1713}_{-1145}$ & $0.5^{+0.23}_{-0.17}$ & $108.8^{+15.7}_{-13.8}$ & $0.69^{+0.1}_{-0.16}$ & 12.2 \\ 
\rowcolor{Gray}34& $\mathrm{GW190620\_030421}$ & $63.5^{+24.7}_{-16.2}$ & $28.0^{+14.5}_{-11.6}$ & $35.9^{+7.7}_{-6.9}$ & $2.3^{+2.6}_{-1.1}$ & $0.26^{+0.23}_{-0.35}$ & $2721^{+1538}_{-1228}$ & $0.47^{+0.21}_{-0.19}$ & $88.5^{+19.4}_{-12.9}$ & $0.72^{+0.11}_{-0.32}$ & 12.0 \\ 
35& $\mathrm{GW190630\_185205}$ & $33.7^{+6.5}_{-5.2}$ & $23.0^{+5.1}_{-4.7}$ & $24.0^{+2.3}_{-1.5}$ & $1.5^{+0.7}_{-0.4}$ & $0.12^{+0.14}_{-0.15}$ & $1192^{+498}_{-409}$ & $0.23^{+0.08}_{-0.07}$ & $54.3^{+4.2}_{-3.9}$ & $0.7^{+0.05}_{-0.09}$ & 15.3 \\ 
\rowcolor{Gray}36& $\mathrm{GW190701\_203306}$ & $55.2^{+10.6}_{-7.4}$ & $41.2^{+8.4}_{-11.4}$ & $41.0^{+5.0}_{-4.8}$ & $1.3^{+0.8}_{-0.3}$ & $-0.09^{+0.22}_{-0.28}$ & $2015^{+691}_{-671}$ & $0.37^{+0.1}_{-

In [9]:
posfile[41]

'./shilpadata/GW190728_064510-PYCBC-POSTERIOR-XPHM.hdf'

In [11]:
a = h5py.File(posfile[41],'r')

In [13]:
np.median(a['samples']['distance'])

999.5106655176525

In [14]:
round(np.median(a['samples']['distance']))

1000

In [ ]:
#+latexpm(chip,chipplus,chipminus,2)+' & '\

'''
if name == 'GW150914\_095045':
        contents += r'1-OGC'+r' & '+r' \\'
    elif name == 'GW151226\_033853':
        contents += r' \\ \hline'
    elif name == 'GW170104\_101158':
        contents += r'2-OGC'+' & '+r' \\'
    elif name == 'GW170823\_131358':
        contents += r' \\ \hline'
    elif name == 'GW190408\_181802':
        contents += r'3-OGC'+' & '+r' \\'
    else:
        contents += r' \\'
'''